# The Uncertainty Problem
Using the moving window analysis, you may have noticed that we are not able to get a good resoltion in time and frequency. This is called the uncertainty problem, which you might have heard from in physics.

Here, we a closer look how the uncertainty problem effects our sweep signal, when we apply the moving window average on this signal.

### Tasks
1. Read the documentation about [scipy's STFT](https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.chirp.html), especially the parameters nperseg, noverlap and nfft
2. Play around with the parameters

In [ ]:
# Preparation: load packages
import os
from obspy.core import read
from obspy.core import UTCDateTime
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import stft, chirp
import pywt

In [ ]:
# Load Chirp signal
dt = 0.01
t = np.arange(0, 5000) * dt
data = chirp(t=t, f0=0.5, f1=25, t1=t[-1])

In [ ]:
# Applying Short-Time Fourier Transform (STFT) on data
freqs, time, S = stft(x=data, fs=1/dt, window='hann', nperseg=256, noverlap=None, nfft=None)

plt.figure(figsize = [15,6])
plt.pcolormesh(time, freqs, np.abs(S))
plt.xlabel("Time (s)")
plt.ylabel("Frequency (Hz)");

# The instantaneous Frequency
The instantaneous frequency is a measure of the dominating frequency at each time instant of a signal and is determined as the time derivative of the instantaneous phase $\phi (t)$. The phase can be obtained by constructing the analytical signal of an arbitrary time series:

$$ 
\hat{s}(t) = s(t) +  i \cdot \mathcal{H} \left( (s(t) \right) = |\hat{s}(t)| \cdot \exp (i \phi (t)),
$$

where $\mathcal{H}$  denotes the Hilbert-Transform. Note, the scipy function [hilbert()](https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.hilbert.html) computes the analytical signal. Now, we can derive the instantaneous phase as

$$
\phi (t) = \arg \left( \frac{Im(\hat{s}(t))}{Re(\hat{s}(t))} \right).
$$

Note, the instantaneous phase is called wrapped phase if it is in the interval $(−\pi, \pi]$ or $[0, 2 \pi)$. To determine the instantaneous frequncy, we need to [unwrap](https://numpy.org/doc/1.18/reference/generated/numpy.unwrap.html) the phase to get a continous function. Finally, the instantaneous frequency can be determined by

$$
f(t) = \frac{1}{2 \pi} \frac{\text{d} \phi (t)}{\text{d} t}
$$

1. Create a time series with 
    1. increasing / decreasing frequncy content, e.g. a [Chirp-Signal](https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.chirp.html)
    2. increasing and decreasing frequency content, i.e. overlapping of two chirp signals (how does the spectrogram looks like?)
3. Write a function that computes the instantaneous frequency (Hint: use np.diff for instantaneous phase derivative, np.unwrap to unwrap the phase.)
4. What is the meaning of $|\hat{s}(t)|$? (Hint: plot it!) 
5. Plot the results of the instantaneous frequnecy

In [ ]:
# Define the signal
dt = 0.01
t = np.arange(0, 5000) * dt
data = chirp(t=t, f0=0.5, f1=25, t1=t[-1])

In [ ]:
# Function for instantaneous frequency
from scipy.signal import hilbert
def istantaneous_frequency(x, dt):
    # To continue

In [ ]:
# Plot results

# The Continuous Wavelet Transform (CWT)

We learned during the STFT about the uncertainty problem. Using the CWT results in a different time-frequency resolution. For high frequency we get poor frequency resolution by good time resoltution, whereas for low frequencies we get poor time resolution bur good frequency resolution. As you can see, there is no recipe when to use STFT, instantaneous frequnecy or CWT, but it is good to know where are the advantages and disadvantages.

The CWT is defined as

$$
\text{CWT}_{a, b} \left(s(t) \right) = \frac{1}{\sqrt{|a|}} ~ \int_{-\infty}^{\infty} s(t) ~ \Psi^\ast \left( \frac{t-b}{a} \right) \text{d} t ~,
$$

where $a$ denotes the scaling factor of the mother wavelet $\Psi(t)$ and $b$ denotes the translation. 
In other words, the CWT is a convolution of the signal $s(t)$ with a conjugate complex and scaled wavelet-function ([here](https://en.wikipedia.org/wiki/Continuous_wavelet_transform) you find a good visualisation). Due to the different scaled wavelets, the CWT reacts well on abruptly changes in the signal.
Usally we get instead of the frequency on the y-axis the scaling factor $a$, but it depends on the center frequency $f_c$ of the scaled wavelet by

$$
f_a = \frac{f_c}{a} .
$$

Luckily it exists a library [pywt](https://pywavelets.readthedocs.io/en/latest/) to compute the CWT with several wavelets.
For the following example we use a [complex Morlet wavelet](https://en.wikipedia.org/wiki/Morlet_wavelet) per default.

#### Tasks

1. Try to plot a time-frequency representation of different signals and compare with results of STFT
2. Use different [mother wavelets](https://pywavelets.readthedocs.io/en/latest/ref/wavelets.html)

In [ ]:
# Display a mother wavelet
wav, a = wavelet = pywt.ContinuousWavelet("cmor2-0.95").wavefun();
plt.plot(a, wav.real, label="real part");
plt.plot(a, wav.imag, label="imag part");
plt.legend();

In [ ]:
def frequency2scale(fmin, fmax, waveletname, dt):
    """
    Computes scales for given frequency values fmin and famx.
    :param fmin: frequency minimum
    :param fmax: frequency maximum
    :param waveletname: name of wavelet
    :param dt: sampling interval (s)
    """

    # Determine lower bound of scales
    scale_start = 0.1
    scale_min = pywt.scale2frequency(waveletname, scale_start)
    while scale_min/dt > fmax:
        scale_start *= 1.1
        scale_min = pywt.scale2frequency(waveletname, scale_start)
    scale_min = round(scale_start, 2)

    # Determine upper bound of scales
    scale_start = 1
    scale_max = pywt.scale2frequency(waveletname, scale_start)
    while scale_max/dt > fmin:
        scale_start *= 1.1
        scale_max = pywt.scale2frequency(waveletname, scale_start)
    scale_max = round(scale_start, 2)

    return scale_min, scale_max

def scaleogram(x, fs, waveletname="cmor2-0.95", fmin=1, fmax=25, num=100):
    """
    Computes CWT of an signal x with sampling rate fs in Hz 
    :param x: time seris
    :param fs: sampling rate
    :param waveletname: name of wavelet
    :param fmin: minimum frequency
    :param fmax: maximum frequency
    :param num: length of scale array
    """

    # Check all input parameters and change them is they do not fit
    dt = 1 / fs
    f_ny = 1 / (2 * dt)  # Nyquist frequency
    if f_ny < fmax:
        fmax = f_ny

    if fmin >= fmax:
        msg = "Min. frequency {} is greater than max. frequency {} to compute scaleograms.".format(fmin, fmax)
        raise ValueError(msg)

    # Determine scales from fmin and fmax
    scale_min, scale_max = frequency2scale(fmin, fmax, waveletname=waveletname, dt=dt)
    scales = np.logspace(np.log10(scale_min), np.log10(scale_max), num=num)

    # Generate scaleogram
    coefficients, frequencies = pywt.cwt(x, scales, waveletname, sampling_period=dt)
    coefficients = np.abs(coefficients)**2
    time = np.linspace(0, dt * len(x), num=len(x))
    
    return frequencies, time, coefficients

In [ ]:
f_cwt, t_cwt, coeff = scaleogram(data, fs=1/(t[1]-t[0]))
plt.figure(figsize=(16, 8))
plt.pcolormesh(t_cwt, f_cwt, np.abs(coeff))
plt.xlabel("Time (s)")
plt.xlabel("Frequency (Hz)");